In [15]:
import nltk
import pandas as pd
import numpy as np
import utils
import re
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation

In [2]:
raw_comments_df = pd.read_csv("raw_comments_59980.csv")

In [3]:
utils.stop_words

{' could',
 '...',
 'a',
 'about',
 'above',
 'after',
 'again',
 'against',
 'ain',
 'all',
 'also',
 'am',
 'an',
 'and',
 'any',
 'are',
 'aren',
 "aren't",
 'as',
 'at',
 'be',
 'because',
 'become',
 'been',
 'before',
 'being',
 'below',
 'between',
 'both',
 'but',
 'by',
 'can',
 'come',
 'couldn',
 "couldn't",
 'd',
 'did',
 'didn',
 "didn't",
 'do',
 'does',
 'doesn',
 "doesn't",
 'doing',
 'don',
 "don't",
 'down',
 'during',
 'each',
 'few',
 'for',
 'from',
 'further',
 'get',
 'had',
 'hadn',
 "hadn't",
 'has',
 'hasn',
 "hasn't",
 'have',
 'haven',
 "haven't",
 'having',
 'he',
 'her',
 'here',
 'hers',
 'herself',
 'him',
 'himself',
 'his',
 'how',
 'http',
 'i',
 'if',
 'in',
 'into',
 'is',
 'isn',
 "isn't",
 'it',
 "it's",
 'its',
 'itself',
 'just',
 'know',
 'like',
 'll',
 'look',
 'm',
 'ma',
 'make',
 'me',
 'mightn',
 "mightn't",
 'more',
 'most',
 'mustn',
 "mustn't",
 'my',
 'myself',
 'name',
 'needn',
 "needn't",
 'no',
 'nor',
 'not',
 'now',
 'o',
 'of',

In [24]:
raw_comments_df["body_tokens"] = raw_comments_df["body"].apply(utils.preprocess_text)

In [6]:
raw_comments_df = raw_comments_df.drop("Unnamed: 0", axis=1)

In [25]:
raw_comments_df.head(30)

author  subreddit  \
0               Wondervv  AskReddit   
1            Nostophobic  AskReddit   
2            A_Horse1273  AskReddit   
3                 paddzz  AskReddit   
4      UrizenTheArchiver  AskReddit   
5             retracnaes  AskReddit   
6           jedi_pljeske  AskReddit   
7         dyselxiccarrot  AskReddit   
8                 baktiv  AskReddit   
9               Deloeboi  AskReddit   
10          smol_bean666  AskReddit   
11            oddweezing  AskReddit   
12  wanderingconspirator  AskReddit   
13           michael2601  AskReddit   
14            Daisyfielf  AskReddit   
15          fallinaditch  AskReddit   
16      UsernameCensored  AskReddit   
17     ThatSingleEridian  AskReddit   
18           poptarts4me  AskReddit   
19        boltforthedoor  AskReddit   
20               ryanire  AskReddit   
21            sleeptonic  AskReddit   
22              Snugbun7  AskReddit   
23             digbipper  AskReddit   
24             Josgre987  AskReddit   
25                luksav  AskReddit   
26           GA_HoneyBee  AskReddit   
27     LostComradeInOhio  AskReddit   
28       violetdwarfstar  AskReddit   
29           WackyJackal  AskReddit   

                                                 body  score  \
0                                   Hitler ans Stalin      1   
1                                        Good luck :D      1   
2                                                Pb&J      1   
3   Sounds like it's by design so you spend more m...      1   
4                                     they were black      1   
5   I would recommend some foam tips like comply. ...      1   
6                                              Eat it      1   
7   I sure as hell didn't come down from the God D...      1   
8   Deal.\n\nJust give me your bank acc info and c...      1   
9                                              Jacket      1   
10  I would - in all caps, write VACCINATE YOUR FU...      1   
11                                        Head first.      1   
12                                             Doctor      1   
13  A cavewoman and a dinosaur having sex then pop...      1   
14  [agrokinesis](https://powerlisting.fandom.com/...      1   
15  Fuck, I wish this was possible for me. I liter...      1   
16                                        So it seems      1   
17   Not mine, but more like my moms. We were at t...      1   
18                            E V E N   K I T T E N S      1   
19   Someone getting shanked by a broken beer bottle.      1   
20                                        Interesting      1   
21                               Save it for tonight.      1   
22  Don't need to draw anything there's already th...      1   
23  for sure, there's very little in the way of li...      1   
24                                                  🔬      1   
25     There's a village somewhere short of an idiot.      1   
26  Continue playing my very first video game camp...      1   
27     "I'm not uncomfortable with just my thoughts."      1   
28  Honestly just draw a huge biggie cheese mural ...      1   
29  That ones good too! But which ending do you th...      1   

                                          body_tokens  \
0                                    [hitler, stalin]   
1                                        [good, luck]   
2                                                  []   
3              [sound, design, spend, money, economy]   
4                                             [black]   
5   [recommend, foam, tip, comply, squeeze, put, l...   
6                                               [eat]   
7   [sure, hell, god, damn, smokey, mountain, cros...   
8   [deal, give, bank, acc, info, credit, card, in...   
9                                            [jacket]   
10                 [cap, write, vaccinate, fuck, kid]   
11                                      [head, first]   
12                                           [doctor]   
13  [cavewoman, dinosaur,

In [26]:
# only interested in rows where the length of the list of clean tokens is > 0, 
# i.e. distinguishing sentences with at least one non-stopword
cleaned_comments_df = raw_comments_df.loc[raw_comments_df["body_tokens"].map(lambda x: len(x)) > 0, :]

In [27]:
cleaned_comments_df

author   subreddit  \
0               Wondervv   AskReddit   
1            Nostophobic   AskReddit   
3                 paddzz   AskReddit   
4      UrizenTheArchiver   AskReddit   
5             retracnaes   AskReddit   
...                  ...         ...   
59975           brad2008  technology   
59976       Darth_Mufasa  technology   
59977             jangxx  technology   
59978         frangelean  technology   
59979       fame_stencil  technology   

                                                    body  score  \
0                                      Hitler ans Stalin      1   
1                                           Good luck :D      1   
3      Sounds like it's by design so you spend more m...      1   
4                                        they were black      1   
5      I would recommend some foam tips like comply. ...      1   
...                                                  ...    ...   
59975         Microsoft. The source of all abominations.      1   
59976  >had a reason not to care\n\nWe usually call t...      8   
59977  But why would that even be a problem? Of cours...     -1   
59978  LTSC still causes me problems. It still wants ...      1   
59979  This sounds great, but how accurate is it? No ...      2   

                                             body_tokens  \
0                                       [hitler, stalin]   
1                                           [good, luck]   
3                 [sound, design, spend, money, economy]   
4                                                [black]   
5      [recommend, foam, tip, comply, squeeze, put, l...   
...                                                  ...   
59975                   [microsoft, source, abomination]   
59976      [reason, care, usually, call, product, owner]   
59977  [even, problem, course, developer, need, analy...   
59978       [ltsc, still, cause, problem, still, update]   
59979            [sound, great, accurate, test, perfect]   

                                      body_tokens_spaced  
0                                          hitler stalin  
1                                              good luck  
3                       sound design spend money economy  
4                                                  black  
5      recommend foam tip comply squeeze put let expa...  
...                                                  ...  
59975                       microsoft source abomination  
59976             reason care usually call product owner  
59977  even problem course developer need analytics f...  
59978              ltsc still cause problem still update  
59979                  sound great accurate test perfect  

[58926 rows x 6 columns]

In [28]:
subreddit_tokens = cleaned_comments_df.groupby("subreddit")["body_tokens"].sum()

In [29]:
explore_df = pd.DataFrame({"Total Number of Tokens": subreddit_tokens.apply(lambda x: len(x)),
                        "Number of Unique Tokens": subreddit_tokens.apply(lambda x: len(set(x)))})

explore_df["Lexical Diversity"] = explore_df['Number of Unique Tokens'] / explore_df['Total Number of Tokens']

explore_df

Total Number of Tokens  Number of Unique Tokens  \
subreddit                                                         
2007scape                          351                      283   
AmItheAsshole                     4979                     1577   
Amd                                874                      531   
AnimalCrossing                     526                      344   
Animemes                           475                      369   
...                                ...                      ...   
witcher                            802                      432   
worldnews                        13823                     3875   
wow                               2382                     1127   
xboxone                           2178                      875   
youtube                            924                      189   

                Lexical Diversity  
subreddit                          
2007scape                0.806268  
AmItheAsshole            0.316730  
Amd                      0.607551  
AnimalCrossing           0.653992  
Animemes                 0.776842  
...                           ...  
witcher                  0.538653  
worldnews                0.280330  
wow                      0.473132  
xboxone                  0.401745  
youtube                  0.204545  

[249 rows x 3 columns]

In [10]:
from collections import Counter
import operator

def wordListToFreqList(wordlist, top_n=10):
    """Compile a list of all words and their frequency of occurence"""
    
    # count each term's number of occurrences
    freqDict = Counter(wordlist)
    
    # sort the frequency dictionary by its values descending and return the items as a list of tuples
    sortedFreqs = sorted(freqDict.items(), key=operator.itemgetter(1), reverse=True)
    
    return sortedFreqs[:top_n]

In [11]:
freqs = subreddit_tokens.apply(lambda tokens: wordListToFreqList(tokens))
freqs

subreddit
2007scape         [(play, 6), (good, 5), (first, 4), (spot, 4), ...
AmItheAsshole     [(post, 65), (nta, 46), (doe, 36), (please, 36...
Amd               [(voltage, 21), (chip, 11), (run, 10), (set, 9...
AnimalCrossing    [(game, 10), (shop, 10), (code, 6), (build, 6)...
Animemes          [(need, 6), (best, 4), (good, 4), (game, 4), (...
                                        ...                        
witcher           [(please, 17), (ciri, 16), (geralt, 16), (witc...
worldnews         [(doe, 86), (even, 71), (country, 70), (see, 6...
wow               [(play, 26), (game, 20), (classic, 20), (playe...
xboxone           [(game, 42), (xbox, 37), (microsoft, 30), (sor...
youtube           [(post, 77), (please, 58), (tag, 55), (doe, 39...
Name: body_tokens, Length: 249, dtype: object

In [ ]:
freqs.index[1]

In [12]:
import math
import matplotlib.pyplot as plt
from matplotlib import gridspec

In [13]:
# Using gridspec allows us to dynamically add subplots in grid
N = len(freqs.keys())
cols = 2
rows = int(math.ceil(N / cols))
gs = gridspec.GridSpec(rows, cols)

# define the figure space for the plots
fig = plt.figure()
fig.set_figheight(N*2)
fig.set_figwidth(20)

# iterate over number of categories to plot each one's top terms
for i in range(N):
    
    # add a plot to the figure
    ax = fig.add_subplot(gs[i])
    ax.set_title(f"Most Frequent Words for: {freqs.index[i]}", fontsize=14, fontweight='bold')
    
    # break the terms and term counts into two lists/tuples
    x,y = zip(*freqs[i])
    #plot the data
    ax.bar(x,y)
    # increase x-label font size
    plt.xticks(fontsize=14)
    # place numeric label on the bar
    for j, v in enumerate(y):
        ax.text(j, v/2, str(v), color='white', fontweight='bold', ha='center')
    

fig.tight_layout()

In [30]:
cleaned_comments_df["body_tokens_spaced"] = cleaned_comments_df["body_tokens"].apply(lambda x: ' '.join(x))

C:\Users\epayn\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [31]:
cleaned_comments_df.head()

author  subreddit  \
0           Wondervv  AskReddit   
1        Nostophobic  AskReddit   
3             paddzz  AskReddit   
4  UrizenTheArchiver  AskReddit   
5         retracnaes  AskReddit   

                                                body  score  \
0                                  Hitler ans Stalin      1   
1                                       Good luck :D      1   
3  Sounds like it's by design so you spend more m...      1   
4                                    they were black      1   
5  I would recommend some foam tips like comply. ...      1   

                                         body_tokens  \
0                                   [hitler, stalin]   
1                                       [good, luck]   
3             [sound, design, spend, money, economy]   
4                                            [black]   
5  [recommend, foam, tip, comply, squeeze, put, l...   

                                  body_tokens_spaced  
0                                      hitler stalin  
1                                          good luck  
3                   sound design spend money economy  
4                                              black  
5  recommend foam tip comply squeeze put let expa...

In [32]:
tf_vectorizer = CountVectorizer()
tf = tf_vectorizer.fit_transform(cleaned_comments_df["body_tokens_spaced"])
tf_feature_names = tf_vectorizer.get_feature_names()

In [33]:
tf_feature_names

['000bc',
 '000hz',
 '000mg',
 '00203s',
 '0076r2',
 '00am',
 '00bfff',
 '00m20s',
 '00min',
 '00pm',
 '00s',
 '01mm',
 '03z',
 '0464465679e2',
 '04t15',
 '0524le',
 '06_warner',
 '06vzq',
 '07scape',
 '09269s',
 '09ukubw3tep41',
 '0_il7k7fv5q',
 '0_o',
 '0a',
 '0a13',
 '0a1qkd9',
 '0a7',
 '0a_note',
 '0ahow',
 '0ahttps',
 '0ahukewjfjpfap7zoahush',
 '0akminder',
 '0alink',
 '0amake',
 '0aofficial',
 '0aoriginal',
 '0aouoobps0w',
 '0apermalink',
 '0apriff',
 '0areason',
 '0aremindme',
 '0areplaceme',
 '0athe',
 '0athis',
 '0b90bpj1ink2qs2d0z3vtu2zisk0',
 '0bfawn70nzc',
 '0cbiquiibahckewjgj4kcz73oahuaaaaahqaaaaaqbq',
 '0ccwb',
 '0dba7ea8',
 '0dcan',
 '0ddescribe',
 '0di',
 '0dmy',
 '0fewp5t',
 '0h2m10s',
 '0h2m15s',
 '0izr5fjy9gsy3nwxxosrqc',
 '0jn1mg8',
 '0l',
 '0m23s',
 '0m615d',
 '0omtmtn7lhi',
 '0p',
 '0p0000acfo',
 '0qotxgy4ckk',
 '0s',
 '0t',
 '0t5succwcbk',
 '0x122d',
 '100',
 '1000',
 '100000023box',
 '100000031box',
 '1000cr',
 '1000hrs',
 '1000km',
 '1000lbs',
 '1000sqf',
 '100

In [34]:
n_topics = 249
lda = LatentDirichletAllocation(n_components=n_topics, random_state=4).fit(tf)

In [35]:
def display_topics(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        print(f"Topic: {topic_idx}")
        print(" ".join([feature_names[i] for i in topic.argsort()[:-n_top_words - 1:-1]]))

n_top_words = 10
display_topics(lda, tf_feature_names, n_top_words)

Topic: 0
win idk earlier judge stats fuckin microsoft trick could see
Topic: 1
culture button fantastic giveaway supply power salary pcpartpicker com void
Topic: 2
card evidence conversation harder rise carry weekend slightly lose seat
Topic: 3
group metal enemy keyboard lake demo previously play inearthed path
Topic: 4
pay money business loan spend cost company month work buy
Topic: 5
tax file return credit income european century owe asian year
Topic: 6
memes update com event reddit www comments begin check community
Topic: 7
suit vibe advance talent joint symbol conquest chin mean imperialism
Topic: 8
virus flu vaccine corona cold common deserve gay covid strain
Topic: 9
america fault connection vent douche scott american guy brick doe
Topic: 10
china sub offer taiwan excite world congratulation post min need
Topic: 11
title question post please mark automatically remove thank action resubmit
Topic: 12
dead morning challenge reward clean border reset african shall hall
Topic: 13
any

you and bore or meat error strange angle flaw repostsleuthbot
Topic: 161
job college league work good wood selfish great still makeup
Topic: 162
scar key mode illegal master aggressive security alot january overwhelm
Topic: 163
adult street collapse exit see really trashy bump pray funniest
Topic: 164
present buddy snow controller storm skip nightmare cod label vacation
Topic: 165
drink accurate evil huh shape cup man epic cooler fantasy
Topic: 166
bed choice favourite pretty naked literal jedi vpn seed trailer
Topic: 167
ton goal quote battle humanity doe success need still whoever
Topic: 168
bus breast tv worldwide contradict punishment wallet spoon give talk
Topic: 169
statement yep covid19 immunity cycle mutation herd unlock spike doc
Topic: 170
store touch grocery alone cough pant face put isolation sneeze
Topic: 171
big space universe exist bang theory doe expand point happen
Topic: 172
dad mom technically task clue party vega best subscription doe
Topic: 173
employee employer co

In [40]:
lda_output = lda.transform(tf)

# column names
topicnames = ["Topic" + str(i) for i in range(n_topics)]

# index names
docnames = ["Doc" + str(i) for i in range(len(cleaned_comments_df))]

# Make the pandas dataframe
df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topicnames, index=docnames)

# Get dominant topic for each document
dominant_topic = np.argmax(df_document_topic.values, axis=1)
df_document_topic['dominant_topic'] = dominant_topic

In [41]:
len(cleaned_comments_df)

58926

In [39]:
# Styling
def color_blue(val):
    color = 'blue' if val > .1 else 'white'
    return 'color: {col}'.format(col=color)

def make_bold(val):
    weight = 700 if val > .1 else 400
    return 'font-weight: {weight}'.format(weight=weight)

# Apply Style
df_document_topics = df_document_topic.head(15).style.applymap(color_blue).applymap(make_bold)
df_document_topics

In [43]:
!pip install pyLDAvis

  Created wheel for pyLDAvis: filename=pyLDAvis-2.1.2-py2.py3-none-any.whl size=97715 sha256=27c243f67b5cc38b23b41a8c5c8a851b2268580f0900e7716c55031ca7173a68
  Stored in directory: C:\Users\epayn\AppData\Local\pip\Cache\wheels\98\71\24\513a99e58bb6b8465bae4d2d5e9dba8f0bef8179e3051ac414
  Created wheel for funcy: filename=funcy-1.14-py2.py3-none-any.whl size=32045 sha256=1b1c996f9c067fa1e6ce880275441f2d0acb0314c167d5ed3b08eb6d3a9661b0
  Stored in directory: C:\Users\epayn\AppData\Local\pip\Cache\wheels\20\5a\d8\1d875df03deae6f178dfdf70238cca33f948ef8a6f5209f2eb
Successfully built pyLDAvis funcy


In [44]:
# module to visualize topics
import pyLDAvis.sklearn
pyLDAvis.enable_notebook()

pyLDAvis.sklearn.prepare(lda, tf, tf_vectorizer, mds='mmds')

C:\Users\epayn\Anaconda3\lib\site-packages\past\builtins\misc.py:4: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Mapping
C:\Users\epayn\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
138   -0.524445  0.072692       1        1  2.615582
207   -0.398628  0.281297       2        1  2.008030
112   -0.485627  0.264324       3        1  1.927316
214   -0.545209  0.079951       4        1  1.663671
4      0.312525  0.021903       5        1  1.651517
...         ...       ...     ...      ...       ...
168    0.356996  0.086074     245        1  0.192606
7     -0.244639  0.187229     246        1  0.186653
78     0.362568 -0.130776     247        1  0.185681
224   -0.116907 -0.303601     248        1  0.179264
194   -0.116579 -0.260549     249        1  0.178377

[249 rows x 5 columns], topic_info=       Category         Freq    Term        Total  loglift  logprob
9384    Default  6692.000000     com  6692.000000  30.0000  30.0000
17734   Default  2221.000000    fuck  2221.000000  29.0000  29.0000
34110   Default  5830.000000  reddit  5830.000000  28.0000  28.0000
45673   Default  5430.000000     www  5430.000000  27.0000  27.0000
40779   Default  2506.000000   thank  2506.000000  26.0000  26.0000
...         ...          ...     ...          ...      ...      ...
31094  Topic249     6.003394     per   434.846116   2.0464  -5.6396
5184   Topic249     6.342381    back  1994.766684   0.5780  -5.5847
15711  Topic249     6.308994    feel  2155.471470   0.4952  -5.5899
5242   Topic249     6.044321     bad  1253.138733   0.9947  -5.6328
19708  Topic249     5.844004  happen  1362.433010   0.8774  -5.6665

[15419 rows x 6 columns], token_table=       Topic      Freq        Term
term                              
12        66  0.676368         03z
23        22  0.489908          0a
23       105  0.489908          0a
27         8  0.920630     0a_note
28         8  0.981416       0ahow
...      ...       ...         ...
46279    236  0.097041  zuckerberg
46304    137  0.783382       zywoo
46307    127  0.721625         zza
46309     82  0.720337         zzz
46311     50  0.797785     zzzquil

[99032 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[139, 208, 113, 215, 5, 217, 39, 202, 35, 193, 172, 212, 44, 75, 21, 151, 218, 9, 224, 77, 7, 109, 213, 210, 182, 58, 29, 12, 42, 81, 20, 137, 157, 54, 133, 148, 115, 114, 238, 104, 90, 24, 64, 198, 38, 176, 97, 162, 70, 123, 102, 68, 67, 141, 105, 175, 171, 11, 245, 6, 197, 138, 240, 1, 76, 111, 86, 80, 239, 152, 108, 63, 232, 106, 131, 158, 207, 15, 96, 93, 143, 59, 244, 183, 69, 221, 28, 74, 3, 110, 179, 82, 99, 57, 129, 51, 229, 223, 26, 142, 153, 145, 204, 159, 220, 91, 219, 121, 84, 134, 194, 246, 132, 214, 127, 237, 154, 23, 48, 168, 40, 18, 55, 149, 177, 118, 180, 200, 112, 188, 83, 89, 34, 150, 241, 186, 226, 85, 243, 27, 66, 120, 103, 242, 206, 4, 30, 192, 22, 166, 189, 43, 135, 156, 117, 92, 128, 230, 216, 78, 41, 234, 228, 155, 140, 147, 2, 126, 71, 248, 163, 191, 174, 184, 247, 100, 25, 87, 227, 50, 16, 65, 173, 136, 72, 203, 98, 116, 161, 33, 130, 119, 170, 165, 160, 45, 107, 56, 167, 190, 209, 49, 101, 178, 231, 144, 146, 199, 94, 187, 32, 46, 181, 10, 47, 14, 233, 36, 124, 62, 235, 61, 52, 236, 185, 125, 37, 201, 19, 164, 95, 205, 17, 13, 122, 222, 31, 60, 196, 53, 73, 88, 211, 249, 169, 8, 79, 225, 195])